In [0]:
%pip install --upgrade pip
%pip install Airtable

Python interpreter will be restarted.
  Using cached pip-23.0.1-py3-none-any.whl (2.1 MB)
  Attempting uninstall: pip
    Found existing installation: pip 21.2.4
    Uninstalling pip-21.2.4:
      Successfully uninstalled pip-21.2.4
Python interpreter will be restarted.
Python interpreter will be restarted.
Python interpreter will be restarted.


### Summary

Goal: Generate an automated report with all reports from the QA sum stats that are valid for each people ID.

There will be 3 stages for this work: 

1. Issues from QA sum stats → retrieve people IDs and issues from QA Summary Stats
2. Report w/additional data points → build a single report which replicates columns from “working list” tab  (all issues for a people ID concatenated) QA Tier 0 and 1 Profiles_CQA
3. Integration w/JIRA + gsheet output and schedule → generate a ticket which includes the gsheet report ready to be worked on.

* Business Owner: Ana Riquezes 
* Script Owner: Anna Soloveva
* Jira Ticket: https://h1insights.atlassian.net/browse/CQA-1249

### Import Libraries

In [0]:
import pyodbc
import pygsheets
import pandas as pd
import numpy as np
from email.mime.text import MIMEText
import importlib
import json
import xlrd
#from fuzzywuzzy import fuzz
#from fuzzywuzzy import process
import jira as js
import sys, os
import pickle
import datetime as date
from datetime import date

In [0]:
as_of = date.today()

In [0]:
%sh
curl https://packages.microsoft.com/keys/microsoft.asc | apt-key add -
curl https://packages.microsoft.com/config/ubuntu/16.04/prod.list > /etc/apt/sources.list.d/mssql-release.list 
apt-get update
ACCEPT_EULA=Y apt-get install msodbcsql17
apt-get -y install unixodbc-dev
sudo apt-get install python3-pip -y
pip3 install --upgrade pyodbc

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100   983  100   983    0     0  28085      0 --:--:-- --:--:-- --:--:-- 28085
OK
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100    79  100    79    0     0   2821      0 --:--:-- --:--:-- --:--:--  2821
Hit:1 http://security.ubuntu.com/ubuntu focal-security InRelease
Get:2 https://packages.microsoft.com/ubuntu/16.04/prod xenial InRelease [2457 B]
Hit:3 https://repos.azul.com/zulu/deb stable InRelease
Hit:4 http://archive.ubuntu.com/ubuntu focal InRelease
Get:5 https://packages.microsoft.com/ubuntu/16.04/prod xenial/main amd64 Packages [202 kB]
Get:6 https://pa

In [0]:
import sys
sys.path.insert(0, '/dbfs/FileStore/shared_uploads/anna.soloveva@h1.co/')
from sql_library2 import Tesseract

### Issues from QA Summary Stats Report

In [0]:
sumstats = pd.read_csv(f"/dbfs/FileStore/tables/cqa_final_df_tier_latest.csv") #final_df_tier rpt_tier_with_tag  cqa_final_df_tier_latest
tags = pd.read_csv(f"/dbfs/FileStore/tables/cqa_tags_latest.csv") #cqa_tags_latest

sumstats = sumstats[['peopleid','Check']].rename(columns = {'peopleid':'PeopleID'})
tags = tags.loc[tags.Tag.isin([10,17])].rename(columns = {'peopleid':'PeopleID'})
print(len(sumstats))
print(len(tags))

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-3152238722430079>:1
----> 1 sumstats = pd.read_csv(f"/dbfs/FileStore/tables/cqa_final_df_tier_latest.csv") #final_df_tier rpt_tier_with_tag  cqa_final_df_tier_latest
      2 tags = pd.read_csv(f"/dbfs/FileStore/tables/cqa_tags_latest.csv") #cqa_tags_latest
      4 sumstats = sumstats[['peopleid','Check']].rename(columns = {'peopleid':'PeopleID'})

NameError: name 'pd' is not defined

In [0]:
#sumstats[sumstats['peopleid'] == 8219845]

In [0]:
#sumstats[sumstats['Check'] == 'Last Name is Null']

In [0]:
tags.PeopleID = tags.PeopleID.astype(str)
tags.Tag = tags.Tag.astype(str)

In [0]:
tags_grouped = tags.sort_values('Tag')
tags_grouped = tags_grouped.groupby('PeopleID').agg({'Tag': lambda x: ' | '.join(x)}).reset_index()
tags_grouped.head()

PeopleID 
 Tag 
 
 
 
 
 0 
 10001107 
 17 
 
 
 1 
 10001880 
 10 
 
 
 2 
 10002385 
 17 
 
 
 3 
 10004167 
 10 
 
 
 4 
 1000594 
 10

In [0]:
sumstats.PeopleID = sumstats.PeopleID.astype(int)
tags_grouped.PeopleID = tags_grouped.PeopleID.astype(int)

In [0]:
sumstats = pd.merge(sumstats,tags_grouped, how = 'inner', on ='PeopleID').sort_values('Check')
sumstats = sumstats.drop_duplicates()
sumstats.head()

PeopleID 
 Check 
 Tag 
 
 
 
 
 28126 
 2847541 
 Affiliation Type and Organization Type Mismatch 
 10 
 
 
 10948 
 4880354 
 Affiliation Type and Organization Type Mismatch 
 10 
 
 
 27226 
 4833936 
 Affiliation Type and Organization Type Mismatch 
 10 
 
 
 27685 
 10021544 
 Affiliation Type and Organization Type Mismatch 
 10 
 
 
 1220 
 10449541 
 Affiliation Type and Organization Type Mismatch 
 10

In [0]:
len(sumstats)

Out[12]: 34497

In [0]:
sumstats_grouped = sumstats.groupby('PeopleID').agg({'Check': lambda x: ' | '.join(x)}).reset_index()
sumstats_grouped2 = sumstats.groupby('PeopleID')['Check'].count()

In [0]:
sumstats_grouped = pd.merge(sumstats_grouped, sumstats_grouped2, how = 'left', on = 'PeopleID' ).rename(columns = {'Check_x':'Check'}).drop(columns = 'Check_y')
sumstats_grouped.head()

PeopleID 
 Check 
 
 
 
 
 0 
 241 
 Multiple Current Work Affiliations(>5) | Same ... 
 
 
 1 
 726 
 Title Mismatch for Affiliation Type 
 
 
 2 
 1121 
 Title Mismatch for Affiliation Type 
 
 
 3 
 1398 
 Multiple Current Work Affiliations(>5) 
 
 
 4 
 2208 
 Multiple Current Work Affiliations(>5) | Title...

In [0]:
sumstats_grouped[sumstats_grouped['PeopleID'] == 8219816]

PeopleID 
 Check 
 
 
 
 
 21148 
 8219816 
 Affiliation Type and Organization Type Mismatch

In [0]:
sumstats_issues = pd.merge(sumstats,sumstats_grouped, how = 'left', on ='PeopleID').drop(columns = {'Check_x'}).rename(columns = {'Check_y':'Issues (to review)'}).drop_duplicates()
#sumstats_issues['Tag 13 Status'] = 'Includes reviewed profiles, Tag 13'
sumstats_issues['Date'] = '' # The same date when QA summary Stats ran, every Tuesday
sumstats_issues['Assignee'] = ''
sumstats_issues = sumstats_issues[['Assignee','Date','PeopleID','Tag','Issues (to review)']] #,'Tag'
sumstats_issues.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Issues (to review) 
 
 
 
 
 0 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 
 
 1 
 
 
 4880354 
 10 
 Affiliation Type and Organization Type Mismatc... 
 
 
 2 
 
 
 4833936 
 10 
 Affiliation Type and Organization Type Mismatch 
 
 
 3 
 
 
 10021544 
 10 
 Affiliation Type and Organization Type Mismatch 
 
 
 4 
 
 
 10449541 
 10 
 Affiliation Type and Organization Type Mismatc...

In [0]:
sumstats_issues[sumstats_issues['PeopleID'] == 8219816]

Assignee 
 Date 
 PeopleID 
 Tag 
 Issues (to review) 
 
 
 
 
 791 
 
 
 8219816 
 10 
 Affiliation Type and Organization Type Mismatch

### Pulling additional information

In [0]:
%sql
show columns in tesseract_curie.people_latest

col_name PeopleID RDSID PDSID GPOID OPID FullName FirstName MiddleName LastName Prefix Suffix Type Designation NPINumber Email PhoneNumber FaxNumber ORCID TwitterURL LinkedInURL FacebookURL OtherSocialMediaURL IsGDPREmailOptout RefreshedDate ExtensionField CreatedBy CreatedDate ModifiedBy ModifiedDate IsActive IsDeleted InActiveReason DeleteReason Generated_filename Version_id IsGDPRPhoneOptout PrimarySpecialty SecondarySpecialty City State Country GeneralOpenPaymentsCount ResearchOpenPaymentsCount ConfAppearancesCount ClinicalTrialscount PubsCount AffiliationsCount MasteredAffiliationsCount OpenPayments_PhysicianID INFERRED_MagAuthorID GeneralOpenPaymentsAmount ResearchOpenPaymentsAmount InternalComments PhoneISD IsDisambigRequired LanguageCode NpiMailingAddressPhone NpiPracticeAddressPhone YouTubeURL WeiboURL IsAcceptingNewPatients IsAcceptingNewPatientsFrom NPI_Reactivation_Date NPI_Deactivation_Date DerivedEmails Tier County District

In [0]:
def ids_extractor(dframe, value):
  print(len(dframe[value].unique()))
  ids = list(dframe[value].unique())
  ids = ','.join(str(v) for v in ids)
  return ids

In [0]:
# Put PeopleMasterID in the list in order to search
ids = ids_extractor(sumstats_issues, 'PeopleID')

24740


In [0]:
df = sql(f"""SELECT p.PeopleID, p.FullName, p.FirstName, p.MiddleName, p.LastName, p.ORCID, p.LinkedInURL, p.TwitterURL, p.Email, p.NPINumber
FROM tesseract_curie.people_latest p
WHERE p.PeopleID in ({ids})""")

info = df.toPandas()#.replace(np.nan, '', regex=True)
display(info)

PeopleID FullName FirstName MiddleName LastName ORCID LinkedInURL TwitterURL Email NPINumber 241 Hisham Elsherbiny Mohamed Elsherbiny Hisham Elsherbiny Mohamed Elsherbiny null https://www.linkedin.com/in/hisham-elsherbiny-59419a53/ null elsherbiny.hisham@mayo.edu 1023435039 726 Anne Lynn Su Chang Anne Lynn Su Chang https://www.linkedin.com/in/anne-chang-8247897/ null alschang@stanford.edu 1013049188 1121 Nancy Lee Harris Nancy Lee Harris https://www.linkedin.com/in/nancy-lee-harris-abaa7b162/ null nlharris@partners.org 1003889445 1398 Harshad C Patel Harshad C Patel https://www.linkedin.com/in/harshad-patel-334762145 null null 1003899543 2208 Anteneh A Tesfaye Anteneh A Tesfaye https://www.linkedin.com/in/anteneh-tesfaye-9342691a https://twitter.com/anteneht tesfayea@karmanos.org 1003128810 3500 Marta Batus Marta null Batus null null null m_batus@rush.edu|marta_batus@rush.edu 1003087768 4006 Matthew Alexander Lunning Matthew Alexander Lunning 0000-0002-2761-7612 https://www.linkedin.com/in/matthew-lunning-52835a101 https://twitter.com/lymphomaphilia mlunning@unmc.edu 1003935081 4075 Jean-Francois Dorval Jean-Francois null Dorval https://www.linkedin.com/in/jean-francois-jeff-dorval-57656890 null jf.dorval@umontreal.ca 1003937251 4697 Middey Damian Middey null Damian null null null 1013938422 4736 Blair Brengle Blair null Brengle null https://www.linkedin.com/in/blair-brengle-27867b156 https://twitter.com/brenglefamily null 1023014420 4882 Jeremy Adler Jeremy null Adler https://linkedin.com/in/jeremy-adler-8888a977 https://twitter.com/jeremyadlermd?lang=en jeradler@umich.edu 1033243191 4935 Keith C Norris Keith C Norris 0000-0003-3071-0700 https://www.linkedin.com/in/keith-norris-2a8a708 https://twitter.com/kcnorris_ucla kcnorris@mednet.ucla.edu|knorris@ucla.edu 1033245808 6642 Christopher Salvatore Graffeo Christopher Salvatore Graffeo https://www.linkedin.com/in/christophergraffeo/ null graffeo.christopher@mayo.edu 1003222738 6775 Sanjat Kanjilal Sanjat null Kanjilal 0000-0002-1221-5725 https://www.linkedin.com/in/sanjat-kanjilal https://twitter.com/SanjatKanjilal skanjilal@bwh.harvard.edu 1023335528 7184 Salvatore Carbone Salvatore null Carbone 0000-0002-8163-0527 https://www.linkedin.com/in/salvatore-carbone-4326706a https://twitter.com/totocarbone scarbone@vcu.edu 1003353939 7286 Usha Sree Chamarthy Usha Sree null Chamarthy https://www.linkedin.com/in/ushasree-chamarthy-a6694691/ null usha.chamarthy@mclaren.org 1033215967 7432 Stuart Jon Spechler Stuart Jon Spechler null https://www.linkedin.com/in/stuart-spechler-92173213b null sspechler@swmail.sw.org 1033222955 7457 Krista Lentine Krista null Lentine 0000-0002-9423-4849 https://www.linkedin.com/in/krista-lentine-md-phd-fasn-fast-2a7297 https://twitter.com/kristalentine krista.lentine@health.slu.edu 1033223961 7762 John Gavend Sonnenberg John Gavend Sonnenberg https://www.linkedin.com/in/john-sonnenberg-345887aa null jsonnenberg@uptownresearch.com 1023090990 8149 Hossein Maymani Hossein null Maymani null https://www.linkedin.com/in/hossein-maymani-30482b145 null null 1023303096 8320 Jeanette Tetrault Jeanette null Tetrault https://www.linkedin.com/in/jeanette-tetrault-81a76298 https://twitter.com/jtetrault17 jeanette.tetrault@yale.edu 1003841321 8395 Jill E Langer Jill E Langer null null Jill.Langer@pennmedicine.upenn.edu|jill.langer@uphs.upenn.edu 1003844192 8418 Leisha Ann Emens Leisha Ann Emens 0000-0002-7694-0731 https://www.linkedin.com/in/leisha-emens-5815441b6 null emensla@upmc.edu|emensle@jhmi.edu 1003845132 10071 Eugene Braunwald Eugene null Braunwald 0000-0002-3472-626X null https://twitter.com/BraunwaldEugene ebraunwald@partners.org 1013942176 11130 Virginia Byers Kraus Virginia Byers Kraus 0000-0001-8173-8258 https://www.linkedin.com/in/virginia-kraus-65a62933 null kraus004@duke.edu|vbk@duke.edu|virginia.kraus@duke.edu 1013091172 11148 David Michael Aronoff David Michael Aronoff 0000-0003-4587-6121 https://www.linkedin.com/in/daronoff https://twitter.com/DMAro

In [0]:
issues_info = pd.merge(sumstats_issues,info, how = 'left', on ='PeopleID')
issues_info.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Issues (to review) 
 FullName 
 FirstName 
 MiddleName 
 LastName 
 ORCID 
 LinkedInURL 
 TwitterURL 
 Email 
 NPINumber 
 
 
 
 
 0 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 None 
 Kebriaei 
 0000-0002-8607-9404 
 None 
 None 
 pkebriae@mdanderson.org 
 1689768475 
 
 
 1 
 
 
 4880354 
 10 
 Affiliation Type and Organization Type Mismatc... 
 David M Ross 
 David 
 M 
 Ross 
 0000-0001-6442-4409 
 https://www.linkedin.com/in/david-roder-54699329/ 
 None 
 d.ross@flinders.edu.au|david.roder@canceraustr... 
 None 
 
 
 2 
 
 
 4833936 
 10 
 Affiliation Type and Organization Type Mismatch 
 Zhiwen Li 
 Zhiwen 
 None 
 Li 
 None 
 None 
 None 
 lizhiwen@pku.edu.cn|lizw@bjmu.edu.cn 
 None 
 
 
 3 
 
 
 10021544 
 10 
 Affiliation Type and Organization Type Mismatch 
 Miguel Srougi 
 Miguel 
 None 
 Srougi 
 None 
 https://www.linkedin.com/in/miguel-srougi-9243... 
 None 
 srougi@terra.com.br 
 None 
 
 
 4 
 
 
 10449541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Petr V Glybochko 
 Petr 
 V 
 Glybochko 
 0000-0002-5541-2251 
 None 
 None 
 glybochko_p_v@staff.sechenov.ru 
 None

### Tags

In [0]:
query1 = f"""SELECT ppm.PeopleID, pptd.projectpersontagid as Tag_13
FROM Tesseract.curie.People_PreMaster ppm 
LEFT JOIN tesseract.pm.people a WITH(NOLOCK) ON ppm.PeopleID = a.peopleid 
LEFT JOIN Tesseract.pm.projectperson prp  WITH(NOLOCK) ON prp.parentid = ppm.PeopleID
LEFT JOIN Tesseract.pm.projectpersontagdetail pptd WITH(NOLOCK) ON pptd.parentid = prp.projectpersonID
WHERE pptd.projectpersontagid = 13 
AND ppm.PeopleID IN ({ids})"""

tag13 = Tesseract.consult(query1)

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Result Shape:  (33856, 2)


In [0]:
issues_info = pd.merge(issues_info,tag13, how = 'left', on ='PeopleID')
issues_info.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Issues (to review) 
 FullName 
 FirstName 
 MiddleName 
 LastName 
 ORCID 
 LinkedInURL 
 TwitterURL 
 Email 
 NPINumber 
 Tag_13 
 
 
 
 
 0 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 None 
 Kebriaei 
 0000-0002-8607-9404 
 None 
 None 
 pkebriae@mdanderson.org 
 1689768475 
 13.0 
 
 
 1 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 None 
 Kebriaei 
 0000-0002-8607-9404 
 None 
 None 
 pkebriae@mdanderson.org 
 1689768475 
 13.0 
 
 
 2 
 
 
 4880354 
 10 
 Affiliation Type and Organization Type Mismatc... 
 David M Ross 
 David 
 M 
 Ross 
 0000-0001-6442-4409 
 https://www.linkedin.com/in/david-roder-54699329/ 
 None 
 d.ross@flinders.edu.au|david.roder@canceraustr... 
 None 
 13.0 
 
 
 3 
 
 
 4833936 
 10 
 Affiliation Type and Organization Type Mismatch 
 Zhiwen Li 
 Zhiwen 
 None 
 Li 
 None 
 None 
 None 
 lizhiwen@pku.edu.cn|lizw@bjmu.edu.cn 
 None 
 13.0 
 
 
 4 
 
 
 10021544 
 10 
 Affiliation Type and Organization Type Mismatch 
 Miguel Srougi 
 Miguel 
 None 
 Srougi 
 None 
 https://www.linkedin.com/in/miguel-srougi-9243... 
 None 
 srougi@terra.com.br 
 None 
 NaN

In [0]:
query1 = f"""SELECT ppm.PeopleID, pptd.projectpersontagid as Tag_15
FROM Tesseract.curie.People_PreMaster ppm 
LEFT JOIN tesseract.pm.people a WITH(NOLOCK) ON ppm.PeopleID = a.peopleid 
LEFT JOIN Tesseract.pm.projectperson prp  WITH(NOLOCK) ON prp.parentid = ppm.PeopleID
LEFT JOIN Tesseract.pm.projectpersontagdetail pptd WITH(NOLOCK) ON pptd.parentid = prp.projectpersonID
WHERE pptd.projectpersontagid = 15
AND ppm.PeopleID IN ({ids})"""

tag15 = Tesseract.consult(query1)

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Result Shape:  (24109, 2)


In [0]:
issues_info = pd.merge(issues_info,tag15, how = 'left', on ='PeopleID')
issues_info.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Issues (to review) 
 FullName 
 FirstName 
 MiddleName 
 LastName 
 ORCID 
 LinkedInURL 
 TwitterURL 
 Email 
 NPINumber 
 Tag_13 
 Tag_15 
 
 
 
 
 0 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 None 
 Kebriaei 
 0000-0002-8607-9404 
 None 
 None 
 pkebriae@mdanderson.org 
 1689768475 
 13.0 
 15.0 
 
 
 1 
 
 
 2847541 
 10 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 None 
 Kebriaei 
 0000-0002-8607-9404 
 None 
 None 
 pkebriae@mdanderson.org 
 1689768475 
 13.0 
 15.0 
 
 
 2 
 
 
 4880354 
 10 
 Affiliation Type and Organization Type Mismatc... 
 David M Ross 
 David 
 M 
 Ross 
 0000-0001-6442-4409 
 https://www.linkedin.com/in/david-roder-54699329/ 
 None 
 d.ross@flinders.edu.au|david.roder@canceraustr... 
 None 
 13.0 
 15.0 
 
 
 3 
 
 
 4833936 
 10 
 Affiliation Type and Organization Type Mismatch 
 Zhiwen Li 
 Zhiwen 
 None 
 Li 
 None 
 None 
 None 
 lizhiwen@pku.edu.cn|lizw@bjmu.edu.cn 
 None 
 13.0 
 15.0 
 
 
 4 
 
 
 10021544 
 10 
 Affiliation Type and Organization Type Mismatch 
 Miguel Srougi 
 Miguel 
 None 
 Srougi 
 None 
 https://www.linkedin.com/in/miguel-srougi-9243... 
 None 
 srougi@terra.com.br 
 None 
 NaN 
 15.0

In [0]:
issues_info = issues_info[['Assignee','Date','PeopleID','Tag','Tag_13','Tag_15','Issues (to review)','FullName','FirstName','MiddleName','LastName','ORCID','LinkedInURL','TwitterURL',	'Email','NPINumber']]

### Merges Counts

In [0]:
sql = """SELECT distinct me.SurvivingID as PeopleID, count(me.SurvivingID) as 'SurvivingID Merged X Times'
FROM tesseract.pm.MergedEntity me WITH(NOLOCK)
WHERE me.SurvivingID IN ({0})
GROUP BY me.SurvivingID""".format(ids)

df = Tesseract.consult(sql)
df.head()

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Result Shape:  (8463, 2)


PeopleID 
 SurvivingID Merged X Times 
 
 
 
 
 0 
 5172360 
 1 
 
 
 1 
 5372159 
 1 
 
 
 2 
 9798704 
 1 
 
 
 3 
 10053711 
 1 
 
 
 4 
 21087165 
 1

In [0]:
sql = """SELECT distinct me.DuplicateID as PeopleID, count(me.DuplicateID) as 'DuplicateID Merged X Times'
FROM tesseract.pm.MergedEntity me WITH(NOLOCK)
WHERE me.DuplicateID IN ({0})
GROUP BY me.DuplicateID""".format(ids)

df1 = Tesseract.consult(sql)
df1.head()

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Result Shape:  (66, 2)


PeopleID 
 DuplicateID Merged X Times 
 
 
 
 
 0 
 4912432 
 1 
 
 
 1 
 5176851 
 1 
 
 
 2 
 10981615 
 1 
 
 
 3 
 4829644 
 1 
 
 
 4 
 4725986 
 1

In [0]:
final_df = pd.merge(issues_info,df, how = 'left', on ='PeopleID')
final_df = pd.merge(final_df,df1, how = 'left', on ='PeopleID')
final_df = final_df.astype(str).replace({'None':'', 'nan':''}).drop_duplicates()
final_df['Status'] = ''
final_df['Issue Type'] = ''
final_df['Incorrect Merger'] = ''
final_df['Surviving ID'] = ''
final_df['Comments'] = ''
final_df['Supporting URL'] = ''
final_df.to_csv(f"/dbfs/FileStore/tables/CQA1249_QA_Tier_0_and_1_Profiles_{as_of}.csv", index = False)
final_df.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Tag_13 
 Tag_15 
 Issues (to review) 
 FullName 
 FirstName 
 MiddleName 
 ... 
 Email 
 NPINumber 
 SurvivingID Merged X Times 
 DuplicateID Merged X Times 
 Status 
 Issue Type 
 Incorrect Merger 
 Surviving ID 
 Comments 
 Supporting URL 
 
 
 
 
 0 
 
 
 2847541 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 
 ... 
 pkebriae@mdanderson.org 
 1689768475 
 
 
 
 
 
 
 
 
 
 
 2 
 
 
 4880354 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 David M Ross 
 David 
 M 
 ... 
 d.ross@flinders.edu.au|david.roder@canceraustr... 
 
 1.0 
 
 
 
 
 
 
 
 
 
 3 
 
 
 4833936 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatch 
 Zhiwen Li 
 Zhiwen 
 
 ... 
 lizhiwen@pku.edu.cn|lizw@bjmu.edu.cn 
 
 1.0 
 
 
 
 
 
 
 
 
 
 4 
 
 
 10021544 
 10 
 
 15.0 
 Affiliation Type and Organization Type Mismatch 
 Miguel Srougi 
 Miguel 
 
 ... 
 srougi@terra.com.br 
 
 1.0 
 
 
 
 
 
 
 
 
 
 5 
 
 
 10449541 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 Petr V Glybochko 
 Petr 
 V 
 ... 
 glybochko_p_v@staff.sechenov.ru 
 
 1.0 
 
 
 
 
 
 
 
 
 
 
 5 rows × 24 columns

In [0]:
len(final_df)

Out[31]: 24740

In [0]:
sql = """SELECT *
FROM tesseract.pm.MergedEntity me WITH(NOLOCK)
WHERE me.SurvivingID IN ({0})
ORDER BY me.SurvivingID""".format(ids)

df2 = Tesseract.consult(sql)
df2.head()

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Result Shape:  (10946, 13)


MergedEntityID 
 DuplicateID 
 SurvivingID 
 CreatedBy 
 createddate 
 ModifiedBy 
 modifieddate 
 Generated_filename 
 Version_id 
 IsActive 
 Comments 
 ParentID 
 IsDeleted 
 
 
 
 
 0 
 19149 
 4937495 
 1398 
 varaprasad.ch@shoregrp.com 
 2020-07-09 08:56:44.760 
 varaprasad.ch@shoregrp.com 
 2020-07-09 08:56:44.760 
 None 
 None 
 True 
 Ticket no:OB-605 
 None 
 False 
 
 
 1 
 72150 
 4825160 
 4075 
 sridhar mahamkali 
 2021-05-26 10:54:56.773 
 sridhar mahamkali 
 2021-05-26 10:54:56.773 
 None 
 None 
 True 
 OB-9500 
 None 
 False 
 
 
 2 
 31007 
 5183852 
 4075 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 None 
 None 
 True 
 OB-4862 
 None 
 False 
 
 
 3 
 133190 
 12007142 
 6642 
 sreedhar buthalapalli 
 2022-05-11 11:02:12.293 
 sreedhar buthalapalli 
 2022-05-11 11:02:12.293 
 None 
 None 
 True 
 OB-15400 
 None 
 False 
 
 
 4 
 29816 
 4593934 
 7184 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 None 
 None 
 True 
 OB-4862 
 None 
 False

In [0]:
merged_df = pd.merge(df2,df, how = 'left', left_on ='SurvivingID', right_on = 'PeopleID')
merged_df = pd.merge(merged_df,df1, how = 'left', left_on ='DuplicateID', right_on = 'PeopleID')
merged_df = merged_df.drop(columns = ['PeopleID_x','PeopleID_y']).astype(str).replace({'None':'', 'nan':''})
merged_df.to_csv(f"/dbfs/FileStore/tables/CQA1249_QA_Tier_0_and_1_Profiles_Merged_{as_of}.csv", index = False)
merged_df.head()

MergedEntityID 
 DuplicateID 
 SurvivingID 
 CreatedBy 
 createddate 
 ModifiedBy 
 modifieddate 
 Generated_filename 
 Version_id 
 IsActive 
 Comments 
 ParentID 
 IsDeleted 
 SurvivingID Merged X Times 
 DuplicateID Merged X Times 
 
 
 
 
 0 
 19149 
 4937495 
 1398 
 varaprasad.ch@shoregrp.com 
 2020-07-09 08:56:44.760 
 varaprasad.ch@shoregrp.com 
 2020-07-09 08:56:44.760 
 
 
 True 
 Ticket no:OB-605 
 
 False 
 1 
 
 
 
 1 
 72150 
 4825160 
 4075 
 sridhar mahamkali 
 2021-05-26 10:54:56.773 
 sridhar mahamkali 
 2021-05-26 10:54:56.773 
 
 
 True 
 OB-9500 
 
 False 
 2 
 
 
 
 2 
 31007 
 5183852 
 4075 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 
 
 True 
 OB-4862 
 
 False 
 2 
 
 
 
 3 
 133190 
 12007142 
 6642 
 sreedhar buthalapalli 
 2022-05-11 11:02:12.293 
 sreedhar buthalapalli 
 2022-05-11 11:02:12.293 
 
 
 True 
 OB-15400 
 
 False 
 1 
 
 
 
 4 
 29816 
 4593934 
 7184 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 sridhar mahamkali 
 2021-01-06 12:15:24.140 
 
 
 True 
 OB-4862 
 
 False 
 1

###Transpose rows to columns for Issues (to review) column

In [0]:
cqa_reports = pd.read_csv(f"/dbfs/FileStore/tables/rpt_tier_with_tag.csv").drop(columns= 'Tag')
cqa_reports

peopleid 
 Affiliation Type and Organization Type Mismatch 
 Affiliation Type is Null 
 Cross Country 
 Cross Country - Broad 
 Duplicate Unique IDS for Tier Broad 
 DuplicateEmail 
 DuplicateLinkedIn 
 DuplicateNPI_Overlap_Pubs 
 DuplicateORCID 
 ... 
 Publications > 100 in a given year 
 Publications before 1950 
 Pubs linked to people with the same FirstLastMiddle name (>1 peopleids) 
 Same First And Last Name But Different Middle Name In GPO 
 Same Organization More than one Affiliation Type 
 Same Registry ID Attached to Multiple People IDs 
 Society Or Journal Affiliation Only 
 Student Title Under Work Affiliation 
 Title Mismatch for Affiliation Type 
 Total Violations 
 
 
 
 
 0 
 4808580 
 0.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 0.0 
 0.0 
 0.0 
 1.0 
 8.0 
 
 
 1 
 4736839 
 0.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 1.0 
 0.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 1.0 
 7.0 
 
 
 2 
 4587040 
 1.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 0.0 
 0.0 
 0.0 
 1.0 
 7.0 
 
 
 3 
 5256630 
 0.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 7.0 
 
 
 4 
 7657252 
 1.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 1.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 7.0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 146937 
 3863572 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 146938 
 3863472 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 0.0 
 0.0 
 1.0 
 
 
 146939 
 3863390 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 146940 
 3863100 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 146941 
 5275352 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 
 146942 rows × 37 columns

In [0]:
cqa_reports.peopleid = cqa_reports.peopleid.astype(int)
final_df.PeopleID = final_df.PeopleID.astype(int)

In [0]:
final_df = pd.merge(final_df,cqa_reports , how = 'left', left_on = 'PeopleID', right_on = 'peopleid' ).drop(columns = 'peopleid')
final_df.head()

Assignee 
 Date 
 PeopleID 
 Tag 
 Tag_13 
 Tag_15 
 Issues (to review) 
 FullName 
 FirstName 
 MiddleName 
 ... 
 Publications > 100 in a given year 
 Publications before 1950 
 Pubs linked to people with the same FirstLastMiddle name (>1 peopleids) 
 Same First And Last Name But Different Middle Name In GPO 
 Same Organization More than one Affiliation Type 
 Same Registry ID Attached to Multiple People IDs 
 Society Or Journal Affiliation Only 
 Student Title Under Work Affiliation 
 Title Mismatch for Affiliation Type 
 Total Violations 
 
 
 
 
 0 
 
 
 2847541 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 Partow Kebriaei 
 Partow 
 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 2.0 
 
 
 1 
 
 
 4880354 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 David M Ross 
 David 
 M 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 2.0 
 
 
 2 
 
 
 4833936 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatch 
 Zhiwen Li 
 Zhiwen 
 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 3 
 
 
 10021544 
 10 
 
 15.0 
 Affiliation Type and Organization Type Mismatch 
 Miguel Srougi 
 Miguel 
 
 ... 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 1.0 
 
 
 4 
 
 
 10449541 
 10 
 13.0 
 15.0 
 Affiliation Type and Organization Type Mismatc... 
 Petr V Glybochko 
 Petr 
 V 
 ... 
 0.0 
 0.0 
 0.0 
 1.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 2.0 
 
 
 
 5 rows × 60 columns

In [0]:
import sys
sys.path.insert(0,'/Workspace/Repos/pablo.flores@h1.co/databricks_helpers/')

from parallel_databricks import Notebook, parallelNotebooks

import sys
sys.path.insert(0, '/Workspace/Repos/pablo.flores@h1.co/sql_tesseract/')
sys.path.insert(0,'/Workspace/Repos/pablo.flores@h1.co/databricks_helpers/')
from sql_library import Harvesting, Tesseract

In [0]:
ids = tuple(final_df['PeopleID'].unique())

In [0]:
country_df = Tesseract.consult(f"""SELECT DISTINCT pp.PeopleID, pp.Country FROM tesseract.curie.people_premaster pp WHERE pp.Country IS NOT NULL AND pp.PeopleID IN {ids}""")

/databricks/python/lib/python3.9/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [0]:
final_df = pd.merge(final_df, country_df, how = 'left', on = 'PeopleID')

In [0]:
print(f'https://dbc-593c2c2d-f6be.cloud.databricks.com/files/tables/CQA1249_QA_Tier_0_and_1_Profiles_{as_of}.csv?o=960084232686341')
print(f'https://dbc-593c2c2d-f6be.cloud.databricks.com/files/tables/CQA1249_QA_Tier_0_and_1_Profiles_Merged_{as_of}.csv?o=960084232686341')

https://dbc-593c2c2d-f6be.cloud.databricks.com/files/tables/CQA1249_QA_Tier_0_and_1_Profiles_2023-03-23.csv?o=960084232686341
https://dbc-593c2c2d-f6be.cloud.databricks.com/files/tables/CQA1249_QA_Tier_0_and_1_Profiles_Merged_2023-03-23.csv?o=960084232686341


### Gsheets and Jira

In [0]:
Client_Secret_file ='/dbfs/FileStore/tables/api_integration_350021_c857e9d75586.json'
API_Name = 'drive'
API_Version = 'v3'
SCOPES = ['https://www.googleapis.com/auth/drive']

today = date.today().strftime("%Y%m%d")

In [0]:
from airtable import Airtable

from email.message import EmailMessage
import smtplib
import mimetypes
import datetime as date

from datetime import date

as_of = date.today()

from google.oauth2.credentials import Credentials
from google_auth_oauthlib.flow import Flow, InstalledAppFlow
from googleapiclient.discovery import build
from googleapiclient.http import MediaFileUpload, MediaIoBaseDownload
from google.auth.transport.requests import Request
from googleapiclient.errors import HttpError

from google.oauth2 import service_account

credentials = service_account.Credentials.from_service_account_file(
    Client_Secret_file)


def sql_to_pd(sql, connect_str):
    cxn = pyodbc.connect(connect_str)
    temp = pd.read_sql(sql, cxn)
    cxn.close()
    return temp


def create_file():
    global gsheetid
    creds = credentials
    service = build('drive','v3',credentials=creds)
    
    file = service.files().create(body=file_metadata, 
                                  fields='id',
                                  supportsAllDrives=True).execute()
    print(file.get('id'))
    gsheetid=file.get('id')
    
def create_issue(project,summary,description):
  
  new_issue = cqa_jira.create_issue(project=project,
                                    summary=summary,
                                    description=description,
                                    issuetype={'name': 'QA Report'},
                                    parent={'key':'CQA-1206'}, # Soft Edit Reports
                                    assignee={'accountId':'5eb4464cacdf9c0b9156f799'}) #Michael Fields
  print (new_issue)

In [0]:
JIRA_API_TOKEN = '0LbBY6F49qwVVHfCyAG800B4' 
cqa_jira = js.JIRA('https://h1insights.atlassian.net',
                  basic_auth=('ana.riquezes@h1.co',
                  JIRA_API_TOKEN))

In [0]:
folder_id = '1EBis_SHlIN6rNrGxhXR2Eyf2v1qJbM-O' # QA Reports -> Q4 2022 -> QA Tier 0 and 1

file_metadata = {
  'name': f'QA Tier 0 and 1 Profiles - {as_of}',
  'parents': [folder_id],
  'mimeType': 'application/vnd.google-apps.spreadsheet'
}

create_file()

1_72L_tATgQDuasNx4EqDKkNV2a_dJu5mM8iAWL7lYpw


In [0]:
# Working List

gc = pygsheets.authorize(service_file= Client_Secret_file) 
rpt = gc.open_by_key(gsheetid)

rpt.sheet1.title = 'Working List'
rpt.sheet1.rows = final_df.shape[0]

In [0]:
rpt.worksheet_by_title('Working List').set_dataframe(final_df,(1,1), fit=False)

In [0]:
# Merged

rpt.add_worksheet('Merged',rows=250, cols=20)
rpt.rows = merged_df.shape[0]
rpt.worksheet_by_title('Merged').set_dataframe(merged_df,(1,1), fit=True)

In [0]:
desc = f"""

QA Tier 0 and 1 Profiles: https://docs.google.com/spreadsheets/d/{gsheetid}

Databricks Notebook: https://dbc-593c2c2d-f6be.cloud.databricks.com/?o=960084232686341#notebook/3152238722430036/command/3152238722431221

Databricks Job: https://dbc-593c2c2d-f6be.cloud.databricks.com/?o=960084232686341#job/283945856998135

"""

create_issue("CQA",f"QA Tier 0 and 1 Profiles - {as_of}",desc)

CQA-1405
